In [8]:
import logging
import re
import numpy
import matplotlib.pyplot as plot
import pickle

from pymongo import MongoClient

from textblob import TextBlob

import nltk
nltk.download('wordnet')
nltk.download('words')
nltk.download('stopwords')
nltk.download('punkt')
nltk.download('brown')
nltk.download('averaged_perceptron_tagger')
from nltk import pos_tag, word_tokenize
from nltk.corpus import wordnet,  words, stopwords
from nltk.stem.wordnet import WordNetLemmatizer

from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer
from gensim.models.ldamodel import LdaModel
from gensim.models.ldamulticore import LdaMulticore
from gensim.models.ldamodel import LdaModel
from gensim.corpora import Dictionary

import pyLDAvis
import pyLDAvis.gensim

from tqdm import tqdm
from pympler import asizeof

from IPython.display import display

[nltk_data] Downloading package wordnet to /Users/ram/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package words to /Users/ram/nltk_data...
[nltk_data]   Package words is already up-to-date!
[nltk_data] Downloading package stopwords to /Users/ram/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to /Users/ram/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package brown to /Users/ram/nltk_data...
[nltk_data]   Package brown is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /Users/ram/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!


In [2]:
english_words = set(words.words())
english_stopwords = set(stopwords.words('english'))

lemmatize = WordNetLemmatizer().lemmatize


In [3]:
# pos_tags: r - adverb, j - adjective, n - noun, v - verb, 
def nouns(text):
    tokens = tokenize(text)
    tokens = clean(tokens)
    
    _nouns = [token for token, pos in pos_tag(tokens) if pos[0] == 'N']
    return _nouns

In [4]:
# pos_tags: r - adverb, j - adjective, n - noun, v - verb, 
def tokenize(text):
    text = text.lower()
    
    re_word = re.compile('^[a-z]+$')
    
    tokens = []
    for token, pos in pos_tag(word_tokenize(text)):
        
        if not bool(re_word.match(token)):
            continue

        lemma = None
        if pos[0] in ['A', 'N', 'R', 'V']:
            lemma = lemmatize(token, pos[0].lower())
        else:
            if token not in english_words and wordnet.morphy(token) is None:
                continue
            lemma = token
            
        tokens.append(lemma)
    return tokens

In [5]:
def clean(tokens):
    tokens = [token for token in tokens if token not in english_stopwords]
    tokens = [token for token in tokens if len(token) > 2]
    return tokens

In [6]:
text = 'Mediocre food, very loud.  Filet mignon au poivre ordered "medium" was virtually raw on one end of the steak with only a hint of sauce.  Very bland. The "famous" fries are greasy strips of potato skins.  House salad was decent.  Service was OK, but the kitchen was painfully slow. 45 minutes to receive entree.  Not impressed.  $100 per person.  Won\'t be back.'

tokens = tokenize(text)
tokens = clean(tokens)
print(tokens)
print()

print(nouns(text))
# nouns = pos_tag(word_tokenize(text))
# TextBlob(tokens).tags


['mediocre', 'food', 'loud', 'filet', 'mignon', 'poivre', 'order', 'medium', 'virtually', 'raw', 'one', 'end', 'steak', 'hint', 'sauce', 'bland', 'famous', 'fry', 'greasy', 'strip', 'potato', 'skin', 'house', 'salad', 'decent', 'service', 'kitchen', 'painfully', 'slow', 'minute', 'receive', 'entree', 'impressed', 'per', 'person', 'back']

['mediocre', 'food', 'filet', 'mignon', 'poivre', 'order', 'medium', 'end', 'steak', 'hint', 'sauce', 'fry', 'strip', 'potato', 'skin', 'house', 'service', 'minute', 'entree', 'person']


In [7]:
# Source: https://stackoverflow.com/questions/44073393/parallelizing-loading-data-from-mongodb-into-python
import multiprocessing
from atpbar import atpbar
from atpbar import register_reporter, find_reporter, flush

def process_cursor(skip_n, limit_n, reporter):
    print('Starting process',skip_n//limit_n,'...')
    
    register_reporter(reporter)
    
    db =  MongoClient(port=27017).yelp
    cursor = db.reviews_sub.find({}, {'text': 1}).sort('_id', 1).skip(skip_n).limit(limit_n)

    reviews = []
    for review in cursor:
        reviews.append(review)
        
    for i in atpbar(range(len(reviews)), name=str(skip_n//limit_n)):
        review = reviews[i]
        if 'text' in review:
            _nouns = nouns(review['text'])
            db.reviews_sub.update_one({'_id': review['_id']}, {'$set': {'nouns': _nouns}})

    print('Completed process',skip_n//limit_n,'...')

n_cores = 8
collection_size = 767985
batch_size = round(collection_size/n_cores+0.5)
skips = range(0, n_cores*batch_size, batch_size)

reporter = find_reporter()
processes = [multiprocessing.Process(target=process_cursor, args=(skip_n,batch_size, reporter)) for skip_n in skips]

for process in processes:
    process.start()

for process in processes:
    process.join()

flush()

Starting process 0 ...
Starting process 1 ...
Starting process 2 ...
Starting process 3 ...
Starting process 4 ...
Starting process 5 ...
Starting process 6 ...
Starting process 7 ...


VBox()

Completed process 5 ...
Completed process 6 ...
Completed process 7 ...
Completed process 2 ...
Completed process 1 ...
Completed process 0 ...
Completed process 3 ...
Completed process 4 ...


In [9]:
mongoClient = MongoClient(port=27017)
db = mongoClient.yelp

In [10]:
tokenized_docs = []
progress = tqdm(total=767985, leave=True, position=0)
cursor = db.reviews_sub.find({}, {'nouns': 1}).sort('_id', 1)
for doc in cursor:
    progress.update(1)
    if 'nouns' in doc:
        tokenized_docs.append(doc['nouns'])

progress.refresh()

100%|██████████| 767985/767985 [00:11<00:00, 68331.08it/s]

True

In [11]:
%%time
dictionary = Dictionary(tokenized_docs)
corpus = [dictionary.doc2bow(tokenized_doc) for tokenized_doc in tokenized_docs]

dictionary.save('dictionary_sub_nouns.pkl')
with open('corpus_sub_nouns.pkl', 'wb') as file:
    pickle.dump(corpus, file)

100%|██████████| 767985/767985 [00:30<00:00, 68331.08it/s]

CPU times: user 47.7 s, sys: 1.29 s, total: 49 s
Wall time: 48.8 s


In [12]:
dictionary = None
corpus = None

with open('dictionary_sub_nouns.pkl', 'rb') as file:
    dictionary = pickle.load(file)
    
with open('corpus_sub_nouns.pkl', 'rb') as file:
    corpus = pickle.load(file)

In [13]:
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)

In [14]:
%%time
num_topics = 30

model = LdaMulticore(corpus, num_topics=num_topics, id2word=dictionary, passes=40)
model.save('model_sub_nouns.h5')

2020-04-11 14:52:18,185 : INFO : using symmetric alpha at 0.03333333333333333
2020-04-11 14:52:18,186 : INFO : using symmetric eta at 0.03333333333333333
2020-04-11 14:52:18,202 : INFO : using serial LDA version on this node
2020-04-11 14:52:18,454 : INFO : running online LDA training, 30 topics, 40 passes over the supplied corpus of 767985 documents, updating every 30000 documents, evaluating every ~300000 documents, iterating 50x with a convergence threshold of 0.001000
2020-04-11 14:52:18,454 : INFO : training LDA model using 15 processes
2020-04-11 14:52:18,545 : INFO : PROGRESS: pass 0, dispatched chunk #0 = documents up to #2000/767985, outstanding queue size 1
2020-04-11 14:52:18,659 : INFO : PROGRESS: pass 0, dispatched chunk #1 = documents up to #4000/767985, outstanding queue size 2
2020-04-11 14:52:18,662 : INFO : PROGRESS: pass 0, dispatched chunk #2 = documents up to #6000/767985, outstanding queue size 3
2020-04-11 14:52:18,666 : INFO : PROGRESS: pass 0, dispatched chunk 

2020-04-11 14:52:23,999 : INFO : topic #29 (0.033): 0.044*"food" + 0.021*"place" + 0.020*"buffet" + 0.013*"eat" + 0.010*"time" + 0.010*"service" + 0.010*"day" + 0.009*"line" + 0.009*"price" + 0.009*"quality"
2020-04-11 14:52:24,020 : INFO : topic #26 (0.033): 0.040*"buffet" + 0.031*"food" + 0.014*"crab" + 0.014*"time" + 0.013*"price" + 0.012*"selection" + 0.012*"place" + 0.011*"service" + 0.011*"line" + 0.010*"vega"
2020-04-11 14:52:24,028 : INFO : topic diff=30.418999, rho=1.000000
2020-04-11 14:52:24,038 : INFO : PROGRESS: pass 0, dispatched chunk #54 = documents up to #110000/767985, outstanding queue size 40
2020-04-11 14:52:24,441 : INFO : PROGRESS: pass 0, dispatched chunk #55 = documents up to #112000/767985, outstanding queue size 35
2020-04-11 14:52:24,445 : INFO : PROGRESS: pass 0, dispatched chunk #56 = documents up to #114000/767985, outstanding queue size 36
2020-04-11 14:52:24,544 : INFO : PROGRESS: pass 0, dispatched chunk #57 = documents up to #116000/767985, outstandin

2020-04-11 14:52:31,161 : INFO : PROGRESS: pass 0, dispatched chunk #94 = documents up to #190000/767985, outstanding queue size 40
2020-04-11 14:52:31,369 : INFO : PROGRESS: pass 0, dispatched chunk #95 = documents up to #192000/767985, outstanding queue size 40
2020-04-11 14:52:31,550 : INFO : PROGRESS: pass 0, dispatched chunk #96 = documents up to #194000/767985, outstanding queue size 40
2020-04-11 14:52:31,762 : INFO : PROGRESS: pass 0, dispatched chunk #97 = documents up to #196000/767985, outstanding queue size 40
2020-04-11 14:52:31,956 : INFO : PROGRESS: pass 0, dispatched chunk #98 = documents up to #198000/767985, outstanding queue size 40
2020-04-11 14:52:32,129 : INFO : PROGRESS: pass 0, dispatched chunk #99 = documents up to #200000/767985, outstanding queue size 40
2020-04-11 14:52:32,291 : INFO : PROGRESS: pass 0, dispatched chunk #100 = documents up to #202000/767985, outstanding queue size 41
2020-04-11 14:52:32,467 : INFO : PROGRESS: pass 0, dispatched chunk #101 = 

2020-04-11 14:52:38,469 : INFO : topic #4 (0.033): 0.042*"food" + 0.031*"buffet" + 0.018*"place" + 0.014*"item" + 0.013*"service" + 0.010*"thing" + 0.010*"eat" + 0.009*"order" + 0.009*"station" + 0.009*"time"
2020-04-11 14:52:38,477 : INFO : topic diff=0.068397, rho=0.113228
2020-04-11 14:52:38,481 : INFO : PROGRESS: pass 0, dispatched chunk #130 = documents up to #262000/767985, outstanding queue size 39
2020-04-11 14:52:38,696 : INFO : PROGRESS: pass 0, dispatched chunk #131 = documents up to #264000/767985, outstanding queue size 37
2020-04-11 14:52:38,699 : INFO : PROGRESS: pass 0, dispatched chunk #132 = documents up to #266000/767985, outstanding queue size 38
2020-04-11 14:52:38,802 : INFO : PROGRESS: pass 0, dispatched chunk #133 = documents up to #268000/767985, outstanding queue size 39
2020-04-11 14:52:39,039 : INFO : PROGRESS: pass 0, dispatched chunk #134 = documents up to #270000/767985, outstanding queue size 38
2020-04-11 14:52:39,285 : INFO : PROGRESS: pass 0, dispatch

2020-04-11 14:52:46,181 : INFO : PROGRESS: pass 0, dispatched chunk #172 = documents up to #346000/767985, outstanding queue size 38
2020-04-11 14:52:46,340 : INFO : PROGRESS: pass 0, dispatched chunk #173 = documents up to #348000/767985, outstanding queue size 38
2020-04-11 14:52:46,501 : INFO : PROGRESS: pass 0, dispatched chunk #174 = documents up to #350000/767985, outstanding queue size 39
2020-04-11 14:52:46,778 : INFO : merging changes from 32000 documents into a model of 767985 documents
2020-04-11 14:52:46,986 : INFO : topic #22 (0.033): 0.060*"food" + 0.036*"service" + 0.025*"place" + 0.016*"price" + 0.014*"buffet" + 0.012*"vega" + 0.012*"portion" + 0.011*"eat" + 0.010*"star" + 0.009*"experience"
2020-04-11 14:52:46,988 : INFO : topic #15 (0.033): 0.023*"order" + 0.020*"food" + 0.018*"chicken" + 0.014*"bacon" + 0.014*"time" + 0.013*"place" + 0.013*"waffle" + 0.012*"egg" + 0.012*"menu" + 0.010*"breakfast"
2020-04-11 14:52:46,990 : INFO : topic #28 (0.033): 0.053*"time" + 0.03

...

2020-04-11 15:45:19,682 : INFO : PROGRESS: pass 39, dispatched chunk #274 = documents up to #550000/767985, outstanding queue size 36
2020-04-11 15:45:19,836 : INFO : PROGRESS: pass 39, dispatched chunk #275 = documents up to #552000/767985, outstanding queue size 36
2020-04-11 15:45:20,100 : INFO : merging changes from 30000 documents into a model of 767985 documents
2020-04-11 15:45:20,291 : INFO : topic #17 (0.033): 0.118*"room" + 0.043*"hotel" + 0.021*"stay" + 0.017*"night" + 0.016*"pool" + 0.014*"check" + 0.014*"bathroom" + 0.013*"desk" + 0.012*"day" + 0.011*"floor"
2020-04-11 15:45:20,293 : INFO : topic #18 (0.033): 0.030*"service" + 0.028*"customer" + 0.027*"call" + 0.023*"manager" + 0.023*"tell" + 0.016*"time" + 0.014*"charge" + 0.013*"day" + 0.013*"phone" + 0.013*"ask"
2020-04-11 15:45:20,294 : INFO : topic #4 (0.033): 0.296*"item" + 0.063*"die" + 0.035*"product" + 0.025*"man" + 0.022*"bone" + 0.017*"stock" + 0.014*"ikea" + 0.013*"marrow" + 0.013*"costco" + 0.011*"pittsburgh"


2020-04-11 15:45:25,149 : INFO : PROGRESS: pass 39, dispatched chunk #308 = documents up to #618000/767985, outstanding queue size 32
2020-04-11 15:45:25,150 : INFO : PROGRESS: pass 39, dispatched chunk #309 = documents up to #620000/767985, outstanding queue size 33
2020-04-11 15:45:25,150 : INFO : PROGRESS: pass 39, dispatched chunk #310 = documents up to #622000/767985, outstanding queue size 34
2020-04-11 15:45:25,209 : INFO : PROGRESS: pass 39, dispatched chunk #311 = documents up to #624000/767985, outstanding queue size 35
2020-04-11 15:45:25,331 : INFO : PROGRESS: pass 39, dispatched chunk #312 = documents up to #626000/767985, outstanding queue size 35
2020-04-11 15:45:25,527 : INFO : PROGRESS: pass 39, dispatched chunk #313 = documents up to #628000/767985, outstanding queue size 35
2020-04-11 15:45:25,595 : INFO : PROGRESS: pass 39, dispatched chunk #314 = documents up to #630000/767985, outstanding queue size 36
2020-04-11 15:45:25,728 : INFO : PROGRESS: pass 39, dispatched

2020-04-11 15:45:31,113 : INFO : topic #15 (0.033): 0.061*"chicken" + 0.033*"order" + 0.024*"sauce" + 0.022*"fry" + 0.022*"flavor" + 0.020*"taste" + 0.020*"food" + 0.016*"portion" + 0.013*"bacon" + 0.012*"side"
2020-04-11 15:45:31,116 : INFO : topic #27 (0.033): 0.023*"word" + 0.016*"life" + 0.015*"city" + 0.012*"world" + 0.012*"chef" + 0.012*"detail" + 0.011*"eye" + 0.010*"experience" + 0.010*"attention" + 0.009*"create"
2020-04-11 15:45:31,118 : INFO : topic #2 (0.033): 0.052*"car" + 0.026*"time" + 0.025*"service" + 0.022*"work" + 0.021*"hair" + 0.017*"job" + 0.014*"day" + 0.014*"price" + 0.013*"look" + 0.013*"company"
2020-04-11 15:45:31,120 : INFO : topic #8 (0.033): 0.098*"breakfast" + 0.061*"egg" + 0.052*"coffee" + 0.030*"place" + 0.025*"brunch" + 0.020*"morning" + 0.020*"pancake" + 0.019*"toast" + 0.017*"order" + 0.017*"food"
2020-04-11 15:45:31,121 : INFO : topic #11 (0.033): 0.059*"roll" + 0.048*"rice" + 0.039*"thai" + 0.024*"beef" + 0.024*"spicy" + 0.021*"dish" + 0.021*"order

2020-04-11 15:45:37,566 : INFO : topic #1 (0.033): 0.075*"hotel" + 0.072*"strip" + 0.056*"casino" + 0.033*"stay" + 0.029*"view" + 0.025*"room" + 0.024*"location" + 0.019*"restaurant" + 0.017*"vega" + 0.013*"walk"
2020-04-11 15:45:37,568 : INFO : topic #17 (0.033): 0.116*"room" + 0.041*"hotel" + 0.021*"stay" + 0.017*"night" + 0.016*"pool" + 0.014*"bathroom" + 0.014*"check" + 0.013*"desk" + 0.012*"day" + 0.011*"floor"
2020-04-11 15:45:37,570 : INFO : topic #18 (0.033): 0.030*"service" + 0.029*"customer" + 0.026*"call" + 0.023*"manager" + 0.022*"tell" + 0.016*"time" + 0.014*"charge" + 0.013*"day" + 0.013*"pay" + 0.013*"ask"
2020-04-11 15:45:37,571 : INFO : topic #13 (0.033): 0.075*"order" + 0.051*"food" + 0.032*"time" + 0.022*"service" + 0.020*"seat" + 0.020*"wait" + 0.019*"table" + 0.018*"minute" + 0.017*"server" + 0.016*"sit"
2020-04-11 15:45:37,576 : INFO : topic diff=0.022021, rho=0.048565
2020-04-11 15:45:39,715 : INFO : -7.840 per-word bound, 229.1 perplexity estimate based on a hel

CPU times: user 28min 41s, sys: 14min 43s, total: 43min 24s
Wall time: 53min 26s


In [15]:
logging.getLogger().setLevel(logging.CRITICAL)

In [16]:
model = LdaModel.load('model_sub_nouns.h5')

In [19]:
lda_display = pyLDAvis.gensim.prepare(model, corpus, dictionary, sort_topics=False)
pyLDAvis.display(lda_display)

In [22]:
n_topics = model.num_topics
n_terms = 30
display(model.show_topics(n_topics, n_terms))

[(0,
  '0.049*"cream" + 0.047*"chocolate" + 0.045*"ice" + 0.028*"coffee" + 0.020*"dessert" + 0.018*"flavor" + 0.017*"taste" + 0.014*"cake" + 0.014*"place" + 0.013*"try" + 0.013*"crepe" + 0.013*"milk" + 0.012*"pastry" + 0.012*"order" + 0.009*"donut" + 0.009*"latte" + 0.009*"butter" + 0.009*"vanilla" + 0.008*"cookie" + 0.008*"sugar" + 0.008*"strawberry" + 0.007*"cooky" + 0.007*"cup" + 0.006*"bakery" + 0.006*"caramel" + 0.006*"thing" + 0.006*"love" + 0.006*"sweet" + 0.006*"shop" + 0.006*"peanut"'),
 (1,
  '0.075*"hotel" + 0.073*"strip" + 0.055*"casino" + 0.033*"stay" + 0.029*"view" + 0.025*"location" + 0.025*"room" + 0.019*"restaurant" + 0.017*"vega" + 0.013*"walk" + 0.011*"bellagio" + 0.011*"pool" + 0.011*"price" + 0.009*"area" + 0.008*"place" + 0.008*"tower" + 0.007*"vegas" + 0.007*"locate" + 0.007*"staff" + 0.007*"property" + 0.007*"bay" + 0.006*"mandalay" + 0.006*"street" + 0.006*"trip" + 0.006*"lot" + 0.006*"aria" + 0.006*"center" + 0.006*"bar" + 0.006*"caesar" + 0.006*"option"'),
 (

In [24]:
n_topics = model.num_topics
n_terms = 30
for i in range(n_topics):
    display(model.show_topic(i, n_terms))

[('cream', 0.048695333),
 ('chocolate', 0.04672193),
 ('ice', 0.04536529),
 ('coffee', 0.028287875),
 ('dessert', 0.019811435),
 ('flavor', 0.017746355),
 ('taste', 0.016902331),
 ('cake', 0.014407623),
 ('place', 0.013984483),
 ('try', 0.013087822),
 ('crepe', 0.012742526),
 ('milk', 0.012540349),
 ('pastry', 0.012458526),
 ('order', 0.01163645),
 ('donut', 0.009152592),
 ('latte', 0.009058425),
 ('butter', 0.009027142),
 ('vanilla', 0.008628544),
 ('cookie', 0.008384966),
 ('sugar', 0.007998891),
 ('strawberry', 0.007796158),
 ('cooky', 0.006878176),
 ('cup', 0.006530665),
 ('bakery', 0.0063683256),
 ('caramel', 0.006317625),
 ('thing', 0.0061614914),
 ('love', 0.005997043),
 ('sweet', 0.0059255417),
 ('shop', 0.005903926),
 ('peanut', 0.005893706)]

[('hotel', 0.07456311),
 ('strip', 0.072611086),
 ('casino', 0.0554425),
 ('stay', 0.032902535),
 ('view', 0.02909238),
 ('location', 0.025240785),
 ('room', 0.025081905),
 ('restaurant', 0.019414727),
 ('vega', 0.016665937),
 ('walk', 0.012667387),
 ('bellagio', 0.011301652),
 ('pool', 0.010843487),
 ('price', 0.010681207),
 ('area', 0.008806893),
 ('place', 0.008313825),
 ('tower', 0.0077737365),
 ('vegas', 0.007264185),
 ('locate', 0.0071542496),
 ('staff', 0.00713774),
 ('property', 0.0068406914),
 ('bay', 0.006511288),
 ('mandalay', 0.0063711475),
 ('street', 0.0061925575),
 ('trip', 0.006192489),
 ('lot', 0.0060418705),
 ('aria', 0.0059999134),
 ('center', 0.0058430913),
 ('bar', 0.0056913686),
 ('caesar', 0.0056764344),
 ('option', 0.005652132)]

[('car', 0.051780824),
 ('time', 0.025889982),
 ('service', 0.025364228),
 ('work', 0.022222908),
 ('job', 0.01698165),
 ('hair', 0.016528212),
 ('day', 0.013924757),
 ('price', 0.013877936),
 ('look', 0.013282698),
 ('company', 0.013083164),
 ('nail', 0.012235501),
 ('experience', 0.011711204),
 ('salon', 0.011524298),
 ('guy', 0.011493092),
 ('move', 0.010776249),
 ('get', 0.010602141),
 ('home', 0.010195523),
 ('sale', 0.009387786),
 ('call', 0.009140499),
 ('purchase', 0.008951089),
 ('appointment', 0.008797435),
 ('vehicle', 0.008605972),
 ('year', 0.007994952),
 ('use', 0.007908415),
 ('week', 0.007859536),
 ('house', 0.007728531),
 ('color', 0.0073915482),
 ('customer', 0.007239421),
 ('hour', 0.0065876953),
 ('everything', 0.0065215128)]

[('soup', 0.050048444),
 ('bowl', 0.042408522),
 ('shrimp', 0.034797564),
 ('pho', 0.03144259),
 ('crab', 0.029780908),
 ('order', 0.025549369),
 ('ramen', 0.022993553),
 ('place', 0.020322986),
 ('pork', 0.016592037),
 ('spicy', 0.016530888),
 ('clam', 0.014371266),
 ('rice', 0.013509666),
 ('lobster', 0.013465312),
 ('taste', 0.012487425),
 ('oyster', 0.01238018),
 ('flavor', 0.012241318),
 ('pan', 0.011858248),
 ('chowder', 0.011772727),
 ('sauce', 0.011112068),
 ('seafood', 0.011043494),
 ('dip', 0.009710475),
 ('salty', 0.008855437),
 ('eat', 0.008657373),
 ('shell', 0.008177975),
 ('try', 0.0076144137),
 ('juicy', 0.0074027176),
 ('pound', 0.0069639296),
 ('roast', 0.0065879407),
 ('pot', 0.0061964686),
 ('toronto', 0.0060536815)]

[('item', 0.31199354),
 ('die', 0.060183182),
 ('product', 0.047807854),
 ('man', 0.023287848),
 ('stock', 0.020920949),
 ('bone', 0.015699385),
 ('costco', 0.013028723),
 ('pittsburgh', 0.012949516),
 ('gluten', 0.011353548),
 ('ikea', 0.01069046),
 ('shelf', 0.010573949),
 ('mani', 0.010417865),
 ('kim', 0.009801174),
 ('marrow', 0.008915447),
 ('district', 0.008911227),
 ('non', 0.008823799),
 ('war', 0.007535375),
 ('source', 0.0068240175),
 ('eyebrow', 0.006350972),
 ('estate', 0.0063158483),
 ('der', 0.006219522),
 ('cart', 0.0057852115),
 ('dairy', 0.005710594),
 ('jewel', 0.004941838),
 ('protein', 0.004872747),
 ('label', 0.0048693363),
 ('taylor', 0.004712993),
 ('babystacks', 0.004506047),
 ('curl', 0.0044932123),
 ('tim', 0.004152633)]

...

[('dinner', 0.050939012),
 ('steak', 0.04944039),
 ('restaurant', 0.030574542),
 ('service', 0.025213795),
 ('reservation', 0.024002455),
 ('meal', 0.023222307),
 ('experience', 0.019140378),
 ('night', 0.01859064),
 ('birthday', 0.015114968),
 ('order', 0.014872701),
 ('waiter', 0.014591506),
 ('food', 0.014533701),
 ('dessert', 0.014103344),
 ('cook', 0.013822145),
 ('appetizer', 0.013362622),
 ('wine', 0.0122348685),
 ('bread', 0.010990112),
 ('course', 0.010294799),
 ('filet', 0.009963952),
 ('view', 0.009677527),
 ('side', 0.009551668),
 ('potato', 0.00948602),
 ('server', 0.008919497),
 ('menu', 0.008249161),
 ('husband', 0.008242921),
 ('wife', 0.00823658),
 ('chef', 0.007807896),
 ('share', 0.007496145),
 ('cocktail', 0.0072962185),
 ('medium', 0.007115675)]

[('buffet', 0.083617456),
 ('food', 0.06151358),
 ('selection', 0.029000489),
 ('station', 0.02239204),
 ('price', 0.01978841),
 ('crab', 0.018974911),
 ('dessert', 0.018077698),
 ('leg', 0.01608996),
 ('eat', 0.016026657),
 ('quality', 0.015551727),
 ('dinner', 0.014928234),
 ('variety', 0.01482553),
 ('section', 0.012205574),
 ('everything', 0.011684931),
 ('thing', 0.010913816),
 ('seafood', 0.01009954),
 ('pay', 0.009950665),
 ('vega', 0.00942227),
 ('lot', 0.0092272945),
 ('rib', 0.009189943),
 ('lunch', 0.008881689),
 ('option', 0.008305477),
 ('line', 0.008053045),
 ('taste', 0.0079508815),
 ('money', 0.007833445),
 ('plate', 0.007793464),
 ('try', 0.007678991),
 ('time', 0.007633104),
 ('bar', 0.007512773),
 ('person', 0.007512768)]

[('word', 0.022874834),
 ('city', 0.015573556),
 ('life', 0.015480857),
 ('world', 0.012072738),
 ('chef', 0.01183615),
 ('detail', 0.01129183),
 ('eye', 0.01112826),
 ('experience', 0.010295466),
 ('attention', 0.009983806),
 ('create', 0.008624872),
 ('god', 0.0077645862),
 ('moment', 0.0072648586),
 ('thank', 0.0070823575),
 ('describe', 0.006763216),
 ('dream', 0.00643369),
 ('face', 0.006187161),
 ('heart', 0.0060471804),
 ('please', 0.006007333),
 ('country', 0.00571405),
 ('yes', 0.0055454806),
 ('level', 0.005119812),
 ('establishment', 0.005018388),
 ('man', 0.004881521),
 ('style', 0.0048100213),
 ('folk', 0.004753428),
 ('fact', 0.004607021),
 ('mind', 0.004396765),
 ('name', 0.0042437254),
 ('team', 0.0042354944),
 ('feature', 0.0041718925)]

[('time', 0.15569645),
 ('place', 0.09849791),
 ('visit', 0.042551547),
 ('year', 0.031831134),
 ('day', 0.02639402),
 ('trip', 0.025587132),
 ('try', 0.021161748),
 ('vega', 0.018696347),
 ('town', 0.018032072),
 ('love', 0.017033141),
 ('thing', 0.016586116),
 ('vegas', 0.014833526),
 ('week', 0.014716237),
 ('friend', 0.0142890345),
 ('review', 0.013907854),
 ('eat', 0.012428078),
 ('everything', 0.012243565),
 ('something', 0.011169418),
 ('get', 0.011079),
 ('experience', 0.008077228),
 ('everyone', 0.0077519114),
 ('weekend', 0.0076944735),
 ('month', 0.007584503),
 ('way', 0.0069824834),
 ('home', 0.0066203997),
 ('people', 0.0065542385),
 ('couple', 0.006112824),
 ('night', 0.0059780576),
 ('look', 0.0056855744),
 ('family', 0.0056614573)]

[('store', 0.03305741),
 ('airport', 0.02286342),
 ('shop', 0.021370394),
 ('lot', 0.020151991),
 ('place', 0.017795322),
 ('park', 0.015525245),
 ('area', 0.015263483),
 ('people', 0.011176821),
 ('thing', 0.010909064),
 ('mall', 0.009816062),
 ('way', 0.009484531),
 ('look', 0.009174649),
 ('walk', 0.0077211508),
 ('price', 0.0074013877),
 ('parking', 0.0071890783),
 ('day', 0.005866995),
 ('get', 0.0054548043),
 ('location', 0.005399053),
 ('sign', 0.005340792),
 ('something', 0.005229483),
 ('street', 0.005198669),
 ('kid', 0.005145604),
 ('shopping', 0.004834303),
 ('visit', 0.004815051),
 ('space', 0.0045643346),
 ('end', 0.0044892835),
 ('fun', 0.004432577),
 ('gift', 0.0043942262),
 ('option', 0.004174541),
 ('gate', 0.004171193)]

In [25]:
text = "Hard to beat this location for table side entertainment"
tokens = tokenize(text)
tokens = clean(tokens)

print(tokens)

bow = dictionary.doc2bow(tokens)
print(bow)
print(model.get_document_topics(bow, minimum_probability=0))

['hard', 'beat', 'location', 'table', 'side', 'entertainment']
[(0, 1), (4, 1), (6, 1), (9, 1), (270, 1), (4684, 1)]
[(0, 0.0047692284), (1, 0.4934677), (2, 0.0047692284), (3, 0.0047692284), (4, 0.0047692284), (5, 0.0047692284), (6, 0.0047692284), (7, 0.0047692284), (8, 0.0047692284), (9, 0.0047692284), (10, 0.0047692284), (11, 0.0047692284), (12, 0.0047692284), (13, 0.37299392), (14, 0.0047692284), (15, 0.0047692284), (16, 0.0047692284), (17, 0.0047692284), (18, 0.0047692284), (19, 0.0047692284), (20, 0.0047692284), (21, 0.0047692284), (22, 0.0047692284), (23, 0.0047692284), (24, 0.0047692284), (25, 0.0047692284), (26, 0.0047692284), (27, 0.0047692284), (28, 0.0047692284), (29, 0.0047692284)]


In [27]:
def extract_topics(text):
    tokens = tokenize(text)
    tokens = clean(tokens)

    bow = dictionary.doc2bow(tokens)
    topics = model.get_document_topics(bow)
    topics = sorted(topics, key=lambda a: -a[1])
    for topic_idx, odds in topics:
        print(model.show_topic(topic_idx, 10))
        print(odds)
        for keyword, _ in model.show_topic(topic_idx, 10):
            if keyword in tokens:
                print(keyword.upper())
    print("-----------")
    print()

In [28]:
# text = "Hard to beat this location for table side entertainment. From people watching to the water show at the Belagio it's fun to watch while enjoying a great cocktail and dinner. See pics for our favorites!"
text = 'Mediocre food, very loud.  Filet mignon au poivre ordered "medium" was virtually raw on one end of the steak with only a hint of sauce.  Very bland. The "famous" fries are greasy strips of potato skins.  House salad was decent.  Service was OK, but the kitchen was painfully slow. 45 minutes to receive entree.  Not impressed.  $100 per person.  Won\'t be back.'
sentences = nltk.tokenize.sent_tokenize(text)

# extract_topics(text)


for sentence in sentences:
    print(sentence)
    extract_topics(sentence)



Mediocre food, very loud.
[('food', 0.16472714), ('service', 0.09502388), ('place', 0.09187267), ('price', 0.04036649), ('staff', 0.026913293), ('restaurant', 0.022324553), ('star', 0.021699268), ('quality', 0.017607776), ('customer', 0.0132076675), ('location', 0.01306318)]
0.7582846
FOOD
-----------

Filet mignon au poivre ordered "medium" was virtually raw on one end of the steak with only a hint of sauce.
[('dinner', 0.050939012), ('steak', 0.04944039), ('restaurant', 0.030574542), ('service', 0.025213795), ('reservation', 0.024002455), ('meal', 0.023222307), ('experience', 0.019140378), ('night', 0.01859064), ('birthday', 0.015114968), ('order', 0.014872701)]
0.53855085
STEAK
ORDER
[('burger', 0.17456755), ('fry', 0.06791912), ('order', 0.030758731), ('onion', 0.020546596), ('place', 0.018508574), ('bun', 0.015889142), ('taste', 0.012667254), ('try', 0.010450514), ('potato', 0.009849899), ('shake', 0.009811288)]
0.38355508
ORDER
-----------

Very bland.
[('chicken', 0.05984926), (

[('line', 0.15480931), ('wait', 0.1320309), ('hour', 0.079727225), ('time', 0.055019855), ('minute', 0.041812222), ('people', 0.035246883), ('flight', 0.02861205), ('get', 0.022805208), ('min', 0.013963849), ('seat', 0.010931446)]
0.25844055
MINUTE
-----------

Not impressed.
[('food', 0.16472714), ('service', 0.09502388), ('place', 0.09187267), ('price', 0.04036649), ('staff', 0.026913293), ('restaurant', 0.022324553), ('star', 0.021699268), ('quality', 0.017607776), ('customer', 0.0132076675), ('location', 0.01306318)]
0.5165518
[('cream', 0.048695333), ('chocolate', 0.04672193), ('ice', 0.04536529), ('coffee', 0.028287875), ('dessert', 0.019811435), ('flavor', 0.017746355), ('taste', 0.016902331), ('cake', 0.014407623), ('place', 0.013984483), ('try', 0.013087822)]
0.016670628
[('hotel', 0.07456311), ('strip', 0.072611086), ('casino', 0.0554425), ('stay', 0.032902535), ('view', 0.02909238), ('location', 0.025240785), ('room', 0.025081905), ('restaurant', 0.019414727), ('vega', 0.016

[('burger', 0.17456755), ('fry', 0.06791912), ('order', 0.030758731), ('onion', 0.020546596), ('place', 0.018508574), ('bun', 0.015889142), ('taste', 0.012667254), ('try', 0.010450514), ('potato', 0.009849899), ('shake', 0.009811288)]
0.01666706
[('breakfast', 0.09570203), ('egg', 0.061482813), ('coffee', 0.05019021), ('place', 0.029559126), ('brunch', 0.026047053), ('pancake', 0.021484517), ('morning', 0.020211179), ('toast', 0.019652635), ('food', 0.017228553), ('order', 0.017089972)]
0.01666706
[('lunch', 0.07602298), ('salad', 0.065938644), ('menu', 0.027204836), ('pasta', 0.022597125), ('option', 0.017167147), ('dinner', 0.01710211), ('meatball', 0.013950093), ('bread', 0.01340167), ('order', 0.013392164), ('restaurant', 0.012722435)]
0.01666706
[('meat', 0.10645429), ('pork', 0.056143228), ('beef', 0.05501304), ('rib', 0.042704027), ('bbq', 0.032001782), ('corn', 0.025330918), ('side', 0.024464022), ('tender', 0.022171263), ('mac', 0.015999235), ('brisket', 0.01598215)]
0.0166670

[('bar', 0.09865904), ('beer', 0.08149759), ('dog', 0.03673319), ('place', 0.036629923), ('selection', 0.035287246), ('drink', 0.032802146), ('food', 0.03024493), ('bartender', 0.022116395), ('hour', 0.018574093), ('sit', 0.016312018)]
0.01668101
[('tea', 0.064774506), ('place', 0.048153926), ('massage', 0.04244597), ('foot', 0.022207098), ('pedicure', 0.02076824), ('spa', 0.02052659), ('chair', 0.018644257), ('tip', 0.013070458), ('milk', 0.012170319), ('boba', 0.012037456)]
0.01668101
[('water', 0.12969269), ('change', 0.065701395), ('dress', 0.054988593), ('oil', 0.03864906), ('tire', 0.021943614), ('package', 0.017921548), ('bottle', 0.014453089), ('glass', 0.009943997), ('suit', 0.00948802), ('michael', 0.008778513)]
0.01668101
[('line', 0.15480931), ('wait', 0.1320309), ('hour', 0.079727225), ('time', 0.055019855), ('minute', 0.041812222), ('people', 0.035246883), ('flight', 0.02861205), ('get', 0.022805208), ('min', 0.013963849), ('seat', 0.010931446)]
0.01668101
[('taco', 0.085